In [1]:
import json
import read_data
import random
import torch
import torch.nn as nn
import torch.nn.functional as F
import torch.optim as optim
import torch.utils.data
from torch.nn.utils.rnn import pack_padded_sequence, pad_packed_sequence
from optparse import OptionParser
import torch.autograd as autograd
from copy import deepcopy
import os
import sys
import pprint
import numpy as np
os.environ["CUDA_VISIBLE_DEVICES"]= "0"
os.environ['CUDA_LAUNCH_BLOCKING'] = "1"
import torch.backends.cudnn as cudnn
cudnn.benchmark = True
torch.manual_seed(1)

from seqeval.metrics import accuracy_score
from seqeval.metrics import classification_report
from seqeval.metrics import f1_score

# from pytorch_pretrained_bert import BertTokenizer, BertModel, BertForMaskedLM

import eval_srl

loading TRAINING data...
# of sentences: 34856
# of arg_types
	total: 124873 (3.5825 arg-per-sent)
	unique: 12
	for each: Counter({'ARG1': 68451, 'ARG0': 18568, 'ARG3': 11060, 'ARGM-LOC': 6468, 'ARG2': 4935, 'ARGM-MNR': 4098, 'ARGM-TMP': 3423, 'ARGM-EXT': 2986, 'ARGM-CAU': 1819, 'ARGM-INS': 1426, 'ARGM-DIR': 1357, 'ARGM-PRP': 282})


# Option

In [2]:
model_dir = './result/model-morp-sum'
if not os.path.exists(model_dir):
    os.makedirs(model_dir)
model_path = model_dir+'/model.pt'

dev_sent = 500
MASKING = False
ARGINFO = True
DPINFO = True

In [3]:
from datetime import datetime
start_time = datetime.now()
today = start_time.strftime('%Y-%m-%d')

In [4]:
# load data
data = read_data.load_trn_data()
trn_conll = read_data.load_trn_nlp()

In [5]:
# input data
# [
#     ['1', '2', '3', '4', '5', '6', '7', '8', '9', '10', '11', '12', '13', '14', '15'], 
#     ['인사동에', '들어서면', '다종다양의', '창호지,', '도자기', '등', '고미술품들이', '진열장에', '즐비하게', '널려져', '있는', '것을', '볼', '수', '있다.'], 
#     ['ARGM-LOC', '-', '-', '-', '-', '-', 'ARG1', 'ARG1', '-', '-', '-', 'ARG1', '-', '-', '-']
# ]

def get_input_data(data):
    result = []
    for sent in data:
        sent_list = []
        
        tok_idx = []
        tok_str = []
        tok_arg = []
        for token in sent:
            tok_idx.append(token[0])
            tok_str.append(token[1])
            tok_arg.append(token[2])
            
        sent_list.append(tok_idx)
        sent_list.append(tok_str)
        sent_list.append(tok_arg)
        result.append(sent_list)
    return result
        
input_data = get_input_data(data)

In [6]:
div = len(input_data) - dev_sent

dev = input_data[div:]
trn = input_data[:div]
gold_file = './dev.data'
print('')
print('### dev data:', len(dev), 'sents')

with open(gold_file,'w') as f:
    dev_list = []
    for i in dev:
        dev_list += i[2]
        
    json.dump(dev_list, f)
    
gold_to_see = './dev.tosee'
with open(gold_to_see,'w') as f:
    dev_list = []
    for i in dev:
        dev_list.append(i[2])
        
    json.dump(dev_list, f)


### dev data: 500 sents


In [7]:
def prepare_idx():
    dp_to_ix, arg_to_ix, morp_to_ix = {},{},{}
    dp_to_ix['null'] = 0
    morp_to_ix['null'] = 0
    
    for sent in trn_conll:
        for token in sent:
            dp = token[11]
            if dp not in dp_to_ix:
                dp_to_ix[dp] = len(dp_to_ix)
                
            morphs = token[2].split('+')
            for morp in morphs:
                if morp not in morp_to_ix:
                    morp_to_ix[morp] = len(morp_to_ix)
    args = ['ARG0', 'ARG1', 'ARG2', 'ARG3', 'ARGM-CAU', 'ARGM-CND', 'ARGM-DIR', 'ARM-DIS', 'ARGM-INS', 'ARGM-LOC', 'ARCM-MNR', 'ARCM-NEG', 'ARCM-PRD', 'ARCM-PRP', 'ARCM-TMP', 'ARCM-ADV', 'ARCM-EXT', '-']
    for i in args:
        if i not in arg_to_ix:
            arg_to_ix[i] = len(arg_to_ix)
    return dp_to_ix, arg_to_ix, morp_to_ix
dp_to_ix, arg_to_ix, morp_to_ix = prepare_idx()
DP_VOCAB_SIZE = len(dp_to_ix)
ARG_VOCAB_SIZE = len(arg_to_ix)
MORP_VOCAB_SIZE = len(morp_to_ix)
print('DP_VOCAB_SIZE:',DP_VOCAB_SIZE)
print('ARG_VOCAB_SIZE:',ARG_VOCAB_SIZE)
print('MORP_VOCAB_SIZE:', MORP_VOCAB_SIZE)

DP_VOCAB_SIZE: 32
ARG_VOCAB_SIZE: 18
MORP_VOCAB_SIZE: 63376


# Load Word2Vec

In [8]:
from gensim.models import Word2Vec
from gensim.models.keyedvectors import KeyedVectors
print('### loading word2vec model...')
wv_model = KeyedVectors.load_word2vec_format("./wordembedding/100_dim_3_window_5mincount_word2vec.model")
print('... is done')

### loading word2vec model...
... is done


In [9]:
def get_word2vec(morp):
    
    vec = torch.rand(100)
    emb = vec.cuda()
    
    try:
        vec = wv_model[morp]
        emb = torch.from_numpy(vec).cuda()
    except KeyboardInterrupt:
        raise
    except:
        pass                

    return emb

# Configuration

In [10]:
configuration = {'token_dim': 100,
                 'feat_dim': 2,
                 'dp_dim': 4,
                 'arg_dim': 4,
                 'lu_pos_dim': 5,
                 'dp_label_dim': 10,
                 'lstm_input_dim': 100,
                 'lstm_dim': 64,
                 'lstm_depth': 2,
                 'hidden_dim': 64,
                 'position_feature_dim': 5,
                 'num_epochs': 20,
                 'learning_rate': 0.001,
                 'dropout_rate': 0.01,
                 'pretrained_embedding_dim': 300,
                 'model_dir': model_dir,
                 'model_path': model_path,
                 'masking': MASKING,
                 'arg_info': ARGINFO
                 }
print('\n### CONFIGURATION ###\n')
pprint.pprint(configuration)
print('')

TOKDIM = configuration['token_dim']
if DPINFO:
    DPDIM = configuration['dp_dim']
else:
    DPDIM = 0
ARGDIM = configuration['arg_dim']
LSTMINPDIM = configuration['lstm_input_dim']
if ARGINFO:
    FEATDIM = configuration['feat_dim']
else:
    FEATDIM = 1
HIDDENDIM = configuration['hidden_dim']
LSTMDEPTH = configuration['lstm_depth']
DROPOUT_RATE = configuration['dropout_rate']
learning_rate = configuration['learning_rate']
NUM_EPOCHS = configuration['num_epochs']

print('\n### YOUR MODEL WILL BE SAVED TO', model_path, '###\n')

with open(model_dir+'/config.json', 'w') as f:
    json.dump(configuration, f, ensure_ascii=False, indent=4)


### CONFIGURATION ###

{'arg_dim': 4,
 'arg_info': True,
 'dp_dim': 4,
 'dp_label_dim': 10,
 'dropout_rate': 0.01,
 'feat_dim': 2,
 'hidden_dim': 64,
 'learning_rate': 0.001,
 'lstm_depth': 2,
 'lstm_dim': 64,
 'lstm_input_dim': 100,
 'lu_pos_dim': 5,
 'masking': False,
 'model_dir': './result/model-morp-sum',
 'model_path': './result/model-morp-sum/model.pt',
 'num_epochs': 20,
 'position_feature_dim': 5,
 'pretrained_embedding_dim': 300,
 'token_dim': 100}


### YOUR MODEL WILL BE SAVED TO ./result/model-morp-sum/model.pt ###



In [11]:
def get_pred_idxs(conll):
    result = []
    preds = [0 for i in range(len(conll))]
    for i in range(len(conll)):
        tok = conll[i]
        if tok[10] == 'VP' or tok[10] == 'VP_MOD' :
            preds = [0 for item in range(len(conll))]
            preds[i] = 1
            result.append(preds)
            
    return result

In [12]:
def get_arg_idxs(pred_idx, conll):
    arg_idxs = [0 for i in range(len(conll))]
    for i in range(len(conll)):
        tok = conll[i]
        if int(tok[8]) == pred_idx:
#             arg_idxs[i] = 1
            arg_pos = tok[-1]
            if arg_pos[:2] == 'NP':
                arg_idxs[i] = 1
                
    return arg_idxs

In [13]:
def get_feature(pred_idx, conll):
    feat_vec = []
    arg_idxs = get_arg_idxs(pred_idx, conll)
    for i in range(len(conll)):
#         tok = conll[i]
        feature = []
        if pred_idx == i:
            feature.append(1)
        else:
            feature.append(0)
        if FEATDIM >= 2:
            feature.append(arg_idxs[i])
        if FEATDIM == 3:
            if i >= pred_idx:
                position = 0
            else:
                position = 1
            feature.append(position)
        feat_vec.append(feature)                
        
    return feat_vec

In [14]:
def prepare_sequence(seq, to_ix):
    vocab = list(to_ix.keys())
    idxs = []
    for w in seq:
        if w in vocab:
            idxs.append(to_ix[w])
        else:
            idxs.append(0)  

    return torch.tensor(idxs).cuda()

In [15]:
def get_dps(conll):
    dps = []
    for tok in conll:
        dp = tok[10]
        dps.append(dp)
    return dps

In [16]:
def get_sentence_vec(tokens, conll):
    result = []
    for i in range(len(tokens)):
        token = tokens[i]
        morps = conll[i][2].split('+')
#         morp_ix = prepare_sequence(morps, morp_to_ix)
        result.append(morps)
    return result

# dev eval

In [17]:
def get_labels_by_tensor(t):
    value, indices = t.max(1)
    score = pow(1, value)
    labels = []
    for i in indices:
        for label, idx in arg_to_ix.items():
            if idx == i:
                pred = label
                labels.append(pred)
                break
    return labels, score            
        
    pred = None
    for label, idx in arg_to_ix.items():
        if idx == indices:
            pred = label
            break
    return pred, score

def eval_dev(my_model):
    
    with torch.no_grad():
        dev_idx = len(input_data)-len(dev)
        result = []
        n = 0    

        pred_file = model_dir+'/dev.result'
        pred_result = open(pred_file,'w')
        
        with open(gold_to_see) as f:
            gold_anno = json.load(f)

        for s_idx in range(len(dev)):
            
            tokens, args = dev[s_idx][1], dev[s_idx][2]

            args_in_all = prepare_sequence(args, arg_to_ix)

            conll = read_data.get_nlp_for_trn(s_idx+dev_idx)
            dps = get_dps(conll)
            dp_in = prepare_sequence(dps, dp_to_ix)

            pred_idxs = get_pred_idxs(conll)
#             features = get_feature(pred_idxs, conll)
#             features = torch.tensor(features).type(torch.cuda.FloatTensor)
            
            pred = ['-' for i in range(len(args))]

            for i in range(len(pred_idxs)):

                pred_seq = pred_idxs[i]
                for j in range(len(pred_seq)):
                    p = pred_seq[j]
                    if p == 1:
                        pred_idx = j
                        
                feature = get_feature(pred_idx, conll)
                feat_vector = torch.tensor(feature).type(torch.cuda.FloatTensor)           
                input_sent = get_sentence_vec(tokens, conll)
                arg_idxs = get_arg_idxs(pred_idx, conll)            
                args_in = torch.zeros(len(arg_idxs))

                for idx in range(len(arg_idxs)):
                    a = arg_idxs[idx]
                    if a == 1:
                        args_in[idx] = args_in_all[idx]
                    else:
                        args_in[idx] = 17

                args_in = args_in.type(torch.cuda.LongTensor)
                
                mask = torch.tensor(arg_idxs).cuda()
                mask = mask.float()

                tag_scores = my_model(input_sent, pred_idx, dp_in, feat_vector, mask)
                
#                 print(tag_scores)
                labels, score = get_labels_by_tensor(tag_scores)

                for idx in range(len(labels)):
                    if arg_idxs[idx] == 1:
                        label = labels[idx]
                    else:
                        label = '-'
                        
                    if label == '-':
                        pass
                    else:
                        if pred[idx] == '-':
                            pred[idx] = label

            pred_result.write(str(pred)+'\n')
            
            annotation = []
            annotation.append(tokens)
            annotation.append(gold_anno[s_idx])
            annotation.append(pred)
            result.append(annotation)
            
#             print(gold_anno[s_idx])
#             print(pred)
     
    
    with open(model_dir+'/dev-result.tosee','w') as f:
        for i in result:
            for j in i:
                f.write(str(j)+'\n')
            f.write('\n')
    
    pred_result.close()
    with open(gold_file,'r') as f:
        gold = json.load(f)
        
    pred = eval_srl.read_prediction(pred_file)    
    f1 = eval_srl.evaluate_from_list(pred, gold)
      
    return f1

In [18]:
# f1 = eval_dev(srl_model)
# print(f1)

# Model

In [27]:
class LSTMTagger(nn.Module):
    
    def __init__(self, tagset_size):
        super(LSTMTagger, self).__init__()
        
        if DPINFO:
            self.dp_embeddings = nn.Embedding(DP_VOCAB_SIZE, DPDIM)
        
        self.lstm_tok = nn.LSTM(LSTMINPDIM+TOKDIM+DPDIM+FEATDIM, HIDDENDIM//2, bidirectional=True, num_layers=LSTMDEPTH, dropout=DROPOUT_RATE)
        self.hidden_lstm_tok = self.init_hidden_lstm_tok()
        
        # Linear
        self.hidden2tag = nn.Linear(HIDDENDIM, tagset_size)
    
    def init_hidden_lstm_tok(self):
        return (torch.zeros(4, 1, HIDDENDIM//2).cuda(),
            torch.zeros(4, 1, HIDDENDIM//2).cuda())
    
    def forward(self, input_sent, pred_idx, dp_in, feat_vector, mask):
        
        if DPINFO:
            dp_embs = self.dp_embeddings(dp_in)
        
#         LSTM layer 1 (subunit to token)
        tok_vectors = []
    
        pred_vec = torch.zeros(100).cuda()
        for morp in input_sent[pred_idx]:
            pred_vec += get_word2vec(morp)
    
        for morps in input_sent:
            we = torch.zeros(100).cuda()
            for morp in morps:
                we += get_word2vec(morp)
            we = torch.cat( (we, pred_vec) )
            tok_vectors.append(we)

        tok_vec = torch.stack(tok_vectors)
        tok_vec = tok_vec.view(len(tok_vec), -1)
        
#         LSTM layer
        if DPINFO:
            input_embs = torch.cat( (tok_vec, dp_embs, feat_vector), 1)
        else:
            input_embs = torch.cat( (tok_vec, feat_vector), 1)
        input_embs_2 = input_embs.view(len(input_embs), 1, -1)

        lstm_out_tok, self.hidden_lstm_tok = self.lstm_tok(
            input_embs_2, self.hidden_lstm_tok)
        
#         lstm_out_tok = F.relu(lstm_out_tok)
        
        # Linear
        tag_space = self.hidden2tag(lstm_out_tok.view(len(input_embs_2),-1))  

        if MASKING:
            for t_idx in range(len(tag_space)):
                t = tag_space[t_idx]
                m = mask[t_idx]
                if m > 0:
#                     if t[-1] >= 0.1:
                    t[-1] = -1
#             for t_idx in range(len(tag_space)):
#                 t = tag_space[t_idx]
#                 m = mask[t_idx]
#                 if m > 0:
#                     pass
#                 else:
#                     t[-1] = 1       
        
#         tag_space = F.relu(tag_space)

#         softmax = nn.Softmax(dim=1)
#         tag_scores = softmax(tag_space)

#         tag_scores = F.relu(tag_space)


#         print(tag_space)
#         softmax = nn.Softmax(dim=1)
#         tag_scores = softmax(tag_space)
        
#         return tag_scores       
        return tag_space

In [20]:
srl_model = LSTMTagger(ARG_VOCAB_SIZE)
srl_model.cuda()
loss_function = nn.CrossEntropyLoss()
# loss_function = nn.NLLLoss()
optimizer = optim.Adam(srl_model.parameters(), lr=learning_rate)
# optimizer = optim.SGD(srl_model.parameters(), lr=learning_rate)

epoch_dev_file = open(model_dir+'/epoch.dev', 'w')
total_step = len(trn)

print('training...')

for epoch in range(NUM_EPOCHS):
    n_of_sent = 0
    total_sent = len(trn)
    for s_idx in range(len(trn)):
        
        tokens, args = trn[s_idx][1], trn[s_idx][2]
        
        
#         print(tokens)
#         print(args)

        args_in_all = prepare_sequence(args, arg_to_ix)

        conll = read_data.get_nlp_for_trn(s_idx)
        dps = get_dps(conll)
        dp_in = prepare_sequence(dps, dp_to_ix)

        pred_idxs = get_pred_idxs(conll)

        for i in range(len(pred_idxs)):      
            
            pred_seq = pred_idxs[i]
            for j in range(len(pred_seq)):
                p = pred_seq[j]
                if p == 1:
                    pred_idx = j
                    
            feature = get_feature(pred_idx, conll)
            feat_vector = torch.tensor(feature).type(torch.cuda.FloatTensor)           
            input_sent = get_sentence_vec(tokens, conll) 
            arg_idxs = get_arg_idxs(pred_idx, conll)            
            args_in = torch.zeros(len(arg_idxs))
            
            for idx in range(len(arg_idxs)):
                a = arg_idxs[idx]
                if a == 1:
                    args_in[idx] = args_in_all[idx]
                else:
                    args_in[idx] = 17
            args_in = args_in.type(torch.cuda.LongTensor)
            
            mask = torch.tensor(arg_idxs).cuda()
            mask = mask.float()
            
            srl_model.zero_grad()         
            srl_model.hidden_lstm_tok = srl_model.init_hidden_lstm_tok()

            tag_scores = srl_model(input_sent, pred_idx, dp_in, feat_vector, mask)
            loss = loss_function(tag_scores, args_in)            
            loss.backward()

            torch.nn.utils.clip_grad_norm_(srl_model.parameters(), 0.25)
            optimizer.step()
            
        n_of_sent +=1
        
        if n_of_sent % 100 == 0:
            print('Epoch [{}/{}], Sent [{}/{}], Loss: {:.4f}' 
                   .format(epoch+1, NUM_EPOCHS, n_of_sent, total_sent, loss.item()))

#         if n_of_sent >= 500:
#             break
            
#         break
        
    # EPOCH 마다 dev에 대한 성능 평가

    torch.save(srl_model, model_path)
    
    f1 = eval_dev(srl_model)
    print('Epoch [{}/{}], F1: {:4f}' 
                   .format(epoch+1, NUM_EPOCHS, f1))
    
    line = 'epoch '+str(epoch+1)+': '+str(f1)+'\n'
    epoch_dev_file.write(line)
    
    end_time = datetime.now()
    print('Duration: {}'.format(end_time - start_time))
    print('')
    
#     break
       
torch.save(srl_model, model_path)
print('')
print('### YOUR MODEL IS SAVED TO', model_path, '###')

training...
tensor([[ 0.1133,  0.1022,  0.1796, -0.0502,  0.0404, -0.0399,  0.0465, -0.1151,
          0.0107, -0.0429,  0.0745, -0.0211,  0.1292,  0.0749, -0.1362,  0.1066,
         -0.0009,  0.0870],
        [ 0.0752,  0.1202,  0.1876, -0.0607,  0.0745, -0.0995,  0.0548, -0.1284,
          0.0267, -0.0799,  0.0747, -0.0627,  0.1553,  0.0345, -0.1395,  0.1093,
         -0.0414,  0.1138],
        [ 0.0678,  0.1104,  0.1861, -0.0426,  0.0582, -0.1014,  0.0603, -0.1215,
          0.0189, -0.0413,  0.0615, -0.0389,  0.1427, -0.0084, -0.1418,  0.0973,
         -0.0216,  0.1217],
        [ 0.0474,  0.1050,  0.1795, -0.0147,  0.0724, -0.0906,  0.0364, -0.0898,
          0.0302, -0.0112,  0.0193, -0.0765,  0.1614, -0.0371, -0.1467,  0.0784,
         -0.0136,  0.1176],
        [ 0.0620,  0.1000,  0.2246, -0.0044,  0.0825, -0.1004,  0.0274, -0.0968,
          0.0491,  0.0053,  0.0373, -0.0704,  0.1735, -0.0477, -0.1573,  0.0578,
         -0.0238,  0.1313],
        [ 0.0399,  0.1066,  0.2057,  0

tensor([[ 0.1161,  0.1236,  0.0614, -0.1368, -0.0301,  0.0573,  0.0679, -0.0844,
          0.0366, -0.0426,  0.0274,  0.0080,  0.1309,  0.1104, -0.0746,  0.1058,
          0.0461,  0.0768],
        [ 0.1187,  0.1122,  0.0589, -0.1682, -0.0319,  0.0020,  0.0444, -0.1053,
          0.0319, -0.0762,  0.0260,  0.0243,  0.1407,  0.0941, -0.0446,  0.1051,
          0.0055,  0.1330],
        [ 0.1002,  0.1171,  0.0217, -0.1372, -0.0435,  0.0421, -0.0156, -0.1065,
          0.0497, -0.0472,  0.0753, -0.0274,  0.1242,  0.1248, -0.0992,  0.0703,
         -0.0037,  0.1824],
        [ 0.1038,  0.1185,  0.0128, -0.1097, -0.0599,  0.0763, -0.0225, -0.0684,
          0.0394, -0.0396,  0.0481, -0.0336,  0.1370,  0.1318, -0.1246,  0.0622,
          0.0209,  0.1802],
        [ 0.0943,  0.1229, -0.0034, -0.1391, -0.0823,  0.0797, -0.0329, -0.0549,
          0.0241, -0.0637,  0.0493, -0.0555,  0.1582,  0.1046, -0.1510,  0.0737,
          0.0098,  0.2120],
        [ 0.0795,  0.1201, -0.0038, -0.1371, -0.11

/usr/local/lib/python3.6/dist-packages/torch/serialization.py:241: UserWarning: Couldn't retrieve source code for container of type LSTMTagger. It won't be checked for correctness upon loading.
  "type " + obj.__name__ + ". It won't be checked "


tensor([[ 0.0837,  0.1421,  0.1934, -0.1458,  0.0175, -0.0882,  0.0472, -0.0900,
          0.0127, -0.1465,  0.0829, -0.0471,  0.1919,  0.0897, -0.0299,  0.1070,
         -0.0440,  0.2391],
        [ 0.0530,  0.1614,  0.2005, -0.1309,  0.0289, -0.0864,  0.0297, -0.1245,
          0.0365, -0.1821,  0.1418, -0.1024,  0.2181,  0.1027, -0.0478,  0.0682,
         -0.0602,  0.3005],
        [ 0.0473,  0.1745,  0.1749, -0.1085,  0.0464, -0.0318,  0.0516, -0.0946,
          0.0272, -0.2209,  0.1713, -0.1279,  0.1831,  0.1051, -0.0709,  0.0964,
         -0.0364,  0.2404],
        [ 0.0454,  0.1610,  0.1675, -0.0893, -0.0131, -0.0741,  0.0374, -0.0801,
          0.0520, -0.1978,  0.1470, -0.1235,  0.1895,  0.0665, -0.0954,  0.0975,
         -0.0530,  0.2316],
        [ 0.0462,  0.1580,  0.1575, -0.1421, -0.0161, -0.0842,  0.0670, -0.0877,
          0.0108, -0.2283,  0.1488, -0.0944,  0.1884,  0.0643, -0.0645,  0.1115,
         -0.0652,  0.2363],
        [ 0.0803,  0.1764,  0.1552, -0.1314,  0.01

tensor([[ 0.1489,  0.2267,  0.1784, -0.0540, -0.0257, -0.0999,  0.0220, -0.0689,
         -0.0101, -0.0934,  0.0024,  0.0478,  0.0927,  0.0424, -0.0359,  0.1433,
          0.0704,  0.1059],
        [ 0.1568,  0.1783,  0.1478, -0.0442, -0.0127, -0.0916,  0.0016, -0.0663,
         -0.0438, -0.0814, -0.0036,  0.1040,  0.0926,  0.0655, -0.0053,  0.1260,
          0.0565,  0.1168],
        [ 0.1778,  0.1562,  0.1572, -0.0597,  0.0033, -0.0879, -0.0241, -0.0763,
          0.0068, -0.0697,  0.0402,  0.0429,  0.0810, -0.0035, -0.0425,  0.1104,
          0.0527,  0.1163],
        [ 0.1895,  0.1500,  0.1444, -0.0806,  0.0109, -0.0917,  0.0023, -0.0774,
          0.0240, -0.0891,  0.0204,  0.0034,  0.0726, -0.0178, -0.0691,  0.0977,
          0.0564,  0.1444],
        [ 0.1912,  0.1239,  0.1129, -0.0652,  0.0279, -0.0846, -0.0141, -0.0762,
         -0.0045, -0.0621,  0.0708,  0.0131,  0.0792, -0.0051, -0.0598,  0.1338,
          0.0584,  0.1453],
        [ 0.1761,  0.1405,  0.1028, -0.0700, -0.01

...

tensor([[-0.0317,  0.2562,  0.0781, -0.0019, -0.0578, -0.1889,  0.0596, -0.0696,
          0.0793, -0.1876,  0.0577,  0.0084,  0.1032,  0.0708, -0.1016,  0.0428,
         -0.0203,  0.1161],
        [-0.0579,  0.2851,  0.0965,  0.0005, -0.0693, -0.1812,  0.0810, -0.0079,
          0.1105, -0.2168,  0.0527, -0.0042,  0.0974,  0.0645, -0.1184,  0.0385,
         -0.0438,  0.1255],
        [-0.0621,  0.3198,  0.0857, -0.0376, -0.0604, -0.1748,  0.0691, -0.0499,
          0.0539, -0.2663,  0.0931, -0.0214,  0.1377,  0.0635, -0.1101,  0.0496,
         -0.0661,  0.1718],
        [-0.0874,  0.2922,  0.0511, -0.0117, -0.1062, -0.1579,  0.0511, -0.0158,
          0.0377, -0.2705,  0.1188, -0.0005,  0.1468,  0.0804, -0.1068,  0.0356,
         -0.0427,  0.1684],
        [-0.0915,  0.2953,  0.1147, -0.0270, -0.0997, -0.1893,  0.0740, -0.0166,
          0.0376, -0.3013,  0.0679, -0.0356,  0.1877,  0.0906, -0.1078,  0.0123,
         -0.0281,  0.1887],
        [-0.0715,  0.3137,  0.1344, -0.0015, -0.09

tensor([[ 0.0673,  0.1971,  0.1489, -0.0676, -0.0834, -0.0845,  0.0693, -0.0726,
          0.0353, -0.1024,  0.0123, -0.0914,  0.1698,  0.0220, -0.1162,  0.0536,
          0.0941,  0.1548],
        [ 0.0514,  0.1434,  0.1529, -0.0823, -0.0893, -0.0613,  0.0835, -0.1109,
          0.0244, -0.0778,  0.0012, -0.0238,  0.1577,  0.0203, -0.0875,  0.0446,
          0.0776,  0.1277],
        [ 0.0500,  0.1126,  0.1619, -0.0732, -0.0531, -0.1062,  0.0567, -0.1184,
          0.0627, -0.0402, -0.0154, -0.0498,  0.1983,  0.0120, -0.0799,  0.0462,
          0.0755,  0.1926],
        [ 0.0245,  0.1582,  0.1281, -0.0661, -0.0636, -0.1088,  0.0195, -0.0739,
          0.0692, -0.0334,  0.0190, -0.0527,  0.1644,  0.0255, -0.0859,  0.0678,
          0.0909,  0.2043],
        [ 0.0420,  0.1607,  0.1658, -0.0607, -0.0406, -0.1449,  0.0090, -0.1203,
          0.0662, -0.0530,  0.0336, -0.0497,  0.2023,  0.0234, -0.0962,  0.0463,
          0.0569,  0.2180],
        [ 0.0316,  0.1642,  0.1656, -0.0603, -0.03

tensor([[ 0.0208,  0.3058,  0.1268, -0.0616,  0.0115, -0.0338,  0.0274, -0.0858,
          0.1327, -0.1365,  0.1159, -0.0828,  0.1694,  0.0683, -0.0983, -0.0035,
          0.0091,  0.1591],
        [ 0.0023,  0.2597,  0.1357, -0.0520, -0.0055,  0.0178,  0.0394, -0.0831,
          0.1118, -0.1346,  0.0797, -0.0410,  0.1467,  0.0649, -0.1139, -0.0132,
         -0.0025,  0.1363],
        [ 0.0095,  0.2486,  0.1284, -0.0809, -0.0332, -0.0464,  0.0366, -0.0896,
          0.1287, -0.1532,  0.1265, -0.0698,  0.1709,  0.0463, -0.1340, -0.0102,
         -0.0559,  0.1568],
        [-0.0511,  0.2687,  0.0221, -0.0683, -0.0568, -0.0019,  0.0157, -0.0194,
          0.1099, -0.2152,  0.1371, -0.0662,  0.1153,  0.0336, -0.1057,  0.0132,
         -0.0328,  0.0809],
        [-0.0217,  0.3096,  0.0564, -0.0692, -0.0668, -0.0076,  0.0392, -0.0504,
          0.0680, -0.1821,  0.0851, -0.0797,  0.1514,  0.0466, -0.1241,  0.0241,
          0.0256,  0.0760],
        [-0.0160,  0.3081,  0.0772, -0.0696, -0.04

tensor([[ 0.0197,  0.3127,  0.1237, -0.0618,  0.0057, -0.0288,  0.0266, -0.0823,
          0.1353, -0.1407,  0.1172, -0.0756,  0.1667,  0.0647, -0.1020, -0.0047,
          0.0041,  0.1566],
        [-0.0088,  0.2698,  0.1303, -0.0505, -0.0032,  0.0258,  0.0390, -0.0780,
          0.1171, -0.1331,  0.0747, -0.0391,  0.1428,  0.0655, -0.1101, -0.0096,
         -0.0056,  0.1301],
        [ 0.0014,  0.2534,  0.1260, -0.0792, -0.0309, -0.0416,  0.0366, -0.0892,
          0.1311, -0.1493,  0.1230, -0.0679,  0.1658,  0.0450, -0.1319, -0.0092,
         -0.0579,  0.1529],
        [-0.0559,  0.2736,  0.0194, -0.0669, -0.0539,  0.0010,  0.0184, -0.0121,
          0.1124, -0.2131,  0.1260, -0.0605,  0.1113,  0.0316, -0.1073,  0.0147,
         -0.0307,  0.0796],
        [-0.0242,  0.3145,  0.0513, -0.0599, -0.0645, -0.0076,  0.0287, -0.0507,
          0.0855, -0.1700,  0.0840, -0.0670,  0.1448,  0.0470, -0.1246,  0.0173,
          0.0268,  0.0825],
        [-0.0209,  0.3115,  0.0715, -0.0637, -0.04

KeyboardInterrupt: 

In [25]:
d = torch.rand(2,2)
softmax = nn.Softmax(dim=0)
d0 = softmax(d)

softmax = nn.Softmax(dim=1)
d1 = softmax(d)

print(d)
print(d0)
print(d1)

tensor([[0.9731, 0.9259],
        [0.7695, 0.1395]])
tensor([[0.5507, 0.6871],
        [0.4493, 0.3129]])
tensor([[0.5118, 0.4882],
        [0.6525, 0.3475]])


In [ ]:
end_time = datetime.now()
print('Duration: {}'.format(end_time - start_time))